### download NASA Ocean Color files 


In [2]:
# setup 

from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter
from IPython.display import JSON
import cartopy
import earthaccess
import matplotlib.pyplot as plt
import numpy as np
import xarray as xr

In [3]:
# NASA earthdata authentication 

auth = earthaccess.login(persist=True)

In [ ]:
# find data 

# MODIS: on board Aqua satellite, collects ocean color 
# processed from Level 1 to Level 4


In [4]:
# data search: 

results = earthaccess.search_datasets(
    keyword="L2 ocean color",
    instrument="MODIS",
)

In [5]:
set((i.summary()["short-name"] for i in results))

{'MODISA_L2_IOP',
 'MODISA_L2_IOP_NRT',
 'MODISA_L2_OC',
 'MODISA_L2_OC_NRT',
 'MODISA_L2_SST',
 'MODISA_L2_SST4',
 'MODISA_L2_SST4_NRT',
 'MODISA_L2_SST_NRT',
 'MODIST_L2_IOP',
 'MODIST_L2_IOP_NRT',
 'MODIST_L2_OC',
 'MODIST_L2_OC_NRT',
 'MODIST_L2_SST',
 'MODIST_L2_SST4',
 'MODIST_L2_SST4_NRT',
 'MODIST_L2_SST_NRT'}

In [ ]:
# resolve timespan and area of interest 
# eg: 
'''
tspan = ("2020-10-15", "2020-10-23")
bbox = (-76.75, 36.97, -75.74, 39.01)
cc = (0, 50) # max 50% cloud cover
'''

In [7]:
# for 123W to 117W
180-123
# -57 
180-117
# -63

63

In [15]:
tspan = ("2024-02-01", "2024-04-01")
# bbox = [lat1, lon1, lat2, lon2
bbox = (-57, 32, -63, 36)


In [16]:
results = earthaccess.search_data(
    short_name="MODISA_L2_OC",
    temporal=tspan,
    bounding_box=bbox,
)

# print info about granules 
results[0]

Collection: {'Version': 'R2022.0', 'ShortName': 'MODISA_L2_OC'}
Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Latitude': 37.45984, 'Longitude': -146.62473}, {'Latitude': 33.8085, 'Longitude': -171.81992}, {'Latitude': 16.55134, 'Longitude': -165.59555}, {'Latitude': 19.67227, 'Longitude': -144.0726}, {'Latitude': 37.45984, 'Longitude': -146.62473}]}}]}}}
Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2024-02-01T00:10:01Z', 'EndingDateTime': '2024-02-01T00:14:59Z'}}
Size(MB): 43.07662105560303
Data: ['https://oceandata.sci.gsfc.nasa.gov/cmr/getfile/AQUA_MODIS.20240201T001001.L2.OC.nc']

In [17]:
data_links = [{"links": i.data_links(), "size (MB):": i.size()} for i in results]
JSON(data_links, expanded=True)
JSON(results)

<IPython.core.display.JSON object>

In [ ]:
# download the data 

paths = earthaccess.download(results, "data")

QUEUEING TASKS | :   0%|          | 0/1225 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/1225 [00:00<?, ?it/s]

Error while downloading the file AQUA_MODIS.20240202T140501.L2.OC.nc
Traceback (most recent call last):
  File "/home/vboatwright/python_environments/sio/lib/python3.12/site-packages/urllib3/response.py", line 748, in _error_catcher
    yield
  File "/home/vboatwright/python_environments/sio/lib/python3.12/site-packages/urllib3/response.py", line 894, in _raw_read
    raise IncompleteRead(self._fp_bytes_read, self.length_remaining)
urllib3.exceptions.IncompleteRead: IncompleteRead(6472186 bytes read, 3424354 more expected)

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/home/vboatwright/python_environments/sio/lib/python3.12/site-packages/earthaccess/store.py", line 682, in _download_file
    shutil.copyfileobj(r.raw, f, length=1024 * 1024)
  File "/usr/lib/python3.12/shutil.py", line 203, in copyfileobj
    while buf := fsrc_read(length):
                 ^^^^^^^^^^^^^^^^^
  File "/home/vboatwright/python_environments/

In [1]:
# plot the data 

prod = xr.open_dataset(paths[0])
obs = xr.open_dataset(paths[0], group="geophysical_data")
nav = xr.open_dataset(paths[0], group="navigation_data")


NameError: name 'xr' is not defined

In [ ]:
# navigation data with geospatial coordinates to merge with geophysical data group (with chl_a product) 

nav = (
    nav
    .set_coords(("longitude", "latitude"))
    .rename({"pixel_control_points": "pixels_per_line"})
)
dataset = xr.merge((prod, obs, nav.coords))



In [ ]:
# xarray method to plot into matplotlib fig


plot = array.plot(
    x="longitude", y="latitude", aspect=2, size=4, cmap="jet", robust=True
)

In [ ]:
# use matplotlib and cartopy to improve vis 

fig = plt.figure(figsize=(10, 7))
ax = plt.axes(projection=cartopy.crs.PlateCarree())
array.plot(x="longitude", y="latitude", cmap="jet", robust=True, ax=ax)
ax.gridlines(draw_labels={"bottom": "x", "left": "y"})
ax.add_feature(cartopy.feature.STATES, linewidth=0.5)
ax.set_title(dataset.attrs["product_name"], loc="center")
plt.show()